In [1]:
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
from tensorflow.keras.preprocessing import image

In [3]:
csv_file = 'age_gender.csv'
data = pd.read_csv(csv_file)

In [5]:
data['pixels'] = data['pixels'].apply(lambda x: np.array(x.split(), dtype='float32').reshape(48, 48))

In [6]:
X = np.stack(data['pixels'].values) / 255.0
X = X.reshape(-1, 48, 48, 1)

In [7]:
y = tf.keras.utils.to_categorical(data['ethnicity'].values)

In [8]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [9]:
model = Sequential([
    Conv2D(32, (3, 3), activation='relu', input_shape=(48, 48, 1)),
    MaxPooling2D((2, 2)),
    Dropout(0.25),
    Conv2D(64, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Dropout(0.25),
    Flatten(),
    Dense(128, activation='relu'),
    Dropout(0.5),
    Dense(y.shape[1], activation='softmax')
])

C:\My programers\Anaconda3\lib\site-packages\keras\src\layers\convolutional\base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [10]:
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

In [11]:
history = model.fit(X_train, y_train, epochs=15, batch_size=32, validation_split=0.2)

Epoch 1/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 26s 41ms/step - accuracy: 0.4639 - loss: 1.3587 - val_accuracy: 0.6283 - val_loss: 1.0296
Epoch 2/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 18s 38ms/step - accuracy: 0.6158 - loss: 1.0309 - val_accuracy: 0.7034 - val_loss: 0.8435
Epoch 3/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 20s 42ms/step - accuracy: 0.6709 - loss: 0.9106 - val_accuracy: 0.7277 - val_loss: 0.7762
Epoch 4/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 26s 54ms/step - accuracy: 0.7032 - loss: 0.8550 - val_accuracy: 0.7400 - val_loss: 0.7392
Epoch 5/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 25s 53ms/step - accuracy: 0.7108 - loss: 0.8231 - val_accuracy: 0.7590 - val_loss: 0.7042
Epoch 6/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 26s 54ms/step - accuracy: 0.7327 - loss: 0.7666 - val_accuracy: 0.7646 - val_loss: 0.6839
Epoch 7/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 39s 50ms/step - accuracy: 0.7380 - loss: 0.7592 - val_accuracy: 0.7712 - val_loss: 0.6759
Epoch 8/15
475/475 ━━━━━━━━━━━━━━━━━━━━ 19s 40ms/step - accuracy: 0.7404 - loss: 0.7417 - 

In [13]:
model.save('face_model.h5')

In [65]:
model = tf.keras.models.load_model('face_model.h5')

def preprocess_image(img_path):
    img = image.load_img(img_path, target_size=(48, 48), color_mode='grayscale')
    img_array = image.img_to_array(img)
    img_array = img_array / 255.0  # Normalizar a [0, 1]
    img_array = np.expand_dims(img_array, axis=0)  # Añadir dimensión para el batch
    img_array = np.expand_dims(img_array, axis=-1)  # Añadir canal (grayscale)
    return img_array

img_path = 'Imagen de WhatsApp 2024-11-26 a las 19.43.22_f81c6787.jpg'
img_array = preprocess_image(img_path)

predictions = model.predict(img_array)

predicted_class = np.argmax(predictions)

print(f"Índice de clase con mayor probabilidad: {predicted_class}")
print(f"Valor de la predicción: {predictions[0][predicted_class]}")

age_classes = ['0-18', '19-25', '26-35', '36-45', '46+']
ethnicity_classes = ['Caucasian', 'Asian', 'African American', 'Latino', 'Other']
gender_classes = ['Male', 'Female']

predicted_age = age_classes[predicted_class]
predicted_ethnicity = ethnicity_classes[predicted_class] 
predicted_gender = gender_classes[predicted_class]

print(f"Predicción de Edad: {predicted_age}")
print(f"Predicción de Etnia: {predicted_ethnicity}")
print(f"Predicción de Género: {predicted_gender}")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 86ms/step
Índice de clase con mayor probabilidad: 1
Valor de la predicción: 0.6104225516319275
Predicción de Edad: 19-25
Predicción de Etnia: Asian
Predicción de Género: Female


741/741 ━━━━━━━━━━━━━━━━━━━━ 6s 7ms/step
Imagen 201:
  Real -> Edad: 1, Género: Masculino, Etnia: 0
  Predicción -> Edad: 0.68, Género: Femenino, Etnia: 1
----------------------------------------


741/741 ━━━━━━━━━━━━━━━━━━━━ 6s 8ms/step
Imagen 1:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 0.92, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 2:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 2.37, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 3:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 0.47, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 4:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 23.76, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 5:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 14.28, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 6:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 9.02, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 7:
  Real -> Edad: 1, Género: 0, Etnia: 2
  Predicción -> Edad: 62.48, Género: F

Imagen 1086:
  Real -> Edad: 1, Género: 1, Etnia: 0
  Predicción -> Edad: 92.80, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 1087:
  Real -> Edad: 1, Género: 1, Etnia: 0
  Predicción -> Edad: 65.40, Género: Femenino, Etnia: 0
----------------------------------------
Imagen 1088:
  Real -> Edad: 1, Género: 1, Etnia: 0
  Predicción -> Edad: 95.80, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 1089:
  Real -> Edad: 1, Género: 1, Etnia: 0
  Predicción -> Edad: 20.23, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 1090:
  Real -> Edad: 1, Género: 1, Etnia: 2
  Predicción -> Edad: 1.48, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 1091:
  Real -> Edad: 1, Género: 1, Etnia: 0
  Predicción -> Edad: 81.52, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 1092:
  Real -> Edad: 1, Género: 1, Etnia: 0
  Predicción -> Edad: 84.46, Género: Femenino, Etnia:

Imagen 1358:
  Real -> Edad: 11, Género: 0, Etnia: 0
  Predicción -> Edad: 97.02, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 1359:
  Real -> Edad: 11, Género: 0, Etnia: 0
  Predicción -> Edad: 94.82, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 1360:
  Real -> Edad: 11, Género: 0, Etnia: 1
  Predicción -> Edad: 37.99, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 1361:
  Real -> Edad: 11, Género: 0, Etnia: 2
  Predicción -> Edad: 14.88, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 1362:
  Real -> Edad: 11, Género: 0, Etnia: 0
  Predicción -> Edad: 97.27, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 1363:
  Real -> Edad: 11, Género: 0, Etnia: 3
  Predicción -> Edad: 2.18, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 1364:
  Real -> Edad: 110, Género: 1, Etnia: 1
  Predicción -> Edad: 12.78, Género: Masculi

Imagen 2307:
  Real -> Edad: 17, Género: 1, Etnia: 0
  Predicción -> Edad: 44.84, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 2308:
  Real -> Edad: 17, Género: 1, Etnia: 0
  Predicción -> Edad: 97.26, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 2309:
  Real -> Edad: 17, Género: 0, Etnia: 0
  Predicción -> Edad: 70.01, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 2310:
  Real -> Edad: 17, Género: 0, Etnia: 0
  Predicción -> Edad: 75.69, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 2311:
  Real -> Edad: 17, Género: 0, Etnia: 1
  Predicción -> Edad: 4.71, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 2312:
  Real -> Edad: 17, Género: 0, Etnia: 1
  Predicción -> Edad: 32.54, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 2313:
  Real -> Edad: 17, Género: 0, Etnia: 1
  Predicción -> Edad: 0.70, Género: Masculin

Imagen 3463:
  Real -> Edad: 21, Género: 0, Etnia: 0
  Predicción -> Edad: 78.61, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 3464:
  Real -> Edad: 21, Género: 0, Etnia: 0
  Predicción -> Edad: 88.93, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 3465:
  Real -> Edad: 21, Género: 0, Etnia: 0
  Predicción -> Edad: 31.29, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 3466:
  Real -> Edad: 21, Género: 0, Etnia: 0
  Predicción -> Edad: 90.14, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 3467:
  Real -> Edad: 21, Género: 1, Etnia: 1
  Predicción -> Edad: 5.37, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 3468:
  Real -> Edad: 21, Género: 0, Etnia: 0
  Predicción -> Edad: 87.94, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 3469:
  Real -> Edad: 21, Género: 0, Etnia: 0
  Predicción -> Edad: 83.64, Género: Femenin

...

Imagen 20706:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 11.90, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 20707:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 2.45, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 20708:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 31.70, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 20709:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 17.27, Género: Femenino, Etnia: 0
----------------------------------------
Imagen 20710:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 1.13, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 20711:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 23.14, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 20712:
  Real -> Edad: 60, Género: 0, Etnia: 3
  Predicción -> Edad: 8.02, Género: M

Imagen 21589:
  Real -> Edad: 67, Género: 0, Etnia: 0
  Predicción -> Edad: 89.00, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 21590:
  Real -> Edad: 67, Género: 0, Etnia: 0
  Predicción -> Edad: 99.15, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 21591:
  Real -> Edad: 67, Género: 0, Etnia: 0
  Predicción -> Edad: 99.35, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 21592:
  Real -> Edad: 67, Género: 0, Etnia: 0
  Predicción -> Edad: 98.57, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 21593:
  Real -> Edad: 67, Género: 0, Etnia: 0
  Predicción -> Edad: 96.12, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 21594:
  Real -> Edad: 67, Género: 1, Etnia: 3
  Predicción -> Edad: 0.11, Género: Femenino, Etnia: 0
----------------------------------------
Imagen 21595:
  Real -> Edad: 67, Género: 0, Etnia: 1
  Predicción -> Edad: 10.43, Género: 

Imagen 22674:
  Real -> Edad: 8, Género: 0, Etnia: 3
  Predicción -> Edad: 24.78, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 22675:
  Real -> Edad: 8, Género: 0, Etnia: 2
  Predicción -> Edad: 0.35, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 22676:
  Real -> Edad: 8, Género: 0, Etnia: 2
  Predicción -> Edad: 0.05, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 22677:
  Real -> Edad: 8, Género: 0, Etnia: 2
  Predicción -> Edad: 16.32, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 22678:
  Real -> Edad: 8, Género: 0, Etnia: 2
  Predicción -> Edad: 37.91, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 22679:
  Real -> Edad: 8, Género: 0, Etnia: 2
  Predicción -> Edad: 12.16, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 22680:
  Real -> Edad: 8, Género: 0, Etnia: 2
  Predicción -> Edad: 0.00, Género: Femenino, Et

Imagen 23660:
  Real -> Edad: 92, Género: 1, Etnia: 0
  Predicción -> Edad: 98.36, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 23661:
  Real -> Edad: 92, Género: 1, Etnia: 0
  Predicción -> Edad: 99.98, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 23662:
  Real -> Edad: 92, Género: 0, Etnia: 3
  Predicción -> Edad: 21.42, Género: Masculino, Etnia: 0
----------------------------------------
Imagen 23663:
  Real -> Edad: 92, Género: 0, Etnia: 2
  Predicción -> Edad: 14.50, Género: Femenino, Etnia: 0
----------------------------------------
Imagen 23664:
  Real -> Edad: 92, Género: 0, Etnia: 0
  Predicción -> Edad: 86.73, Género: Femenino, Etnia: 1
----------------------------------------
Imagen 23665:
  Real -> Edad: 92, Género: 1, Etnia: 0
  Predicción -> Edad: 99.97, Género: Masculino, Etnia: 1
----------------------------------------
Imagen 23666:
  Real -> Edad: 93, Género: 1, Etnia: 0
  Predicción -> Edad: 99.89, Género:

C:\My programers\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\My programers\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\My programers\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [56]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler

# Cargar los datos desde el archivo CSV
df = pd.read_csv('age_gender.csv')

# Preprocesamiento de imágenes
# Convertir la columna 'pixels' en un array de píxeles
X = df['pixels'].apply(lambda x: np.array(x.split(), dtype=int))

# Hacer que X sea una matriz con una fila por cada imagen
X = np.stack(X)

# Estandarizar los valores de los píxeles
scaler = StandardScaler()
X = scaler.fit_transform(X)

# Etiquetas (y): edad, etnia y género
y_age = df['age']
y_ethnicity = df['ethnicity']
y_gender = df['gender']

# Codificar las etiquetas categóricas
encoder_ethnicity = LabelEncoder()
y_ethnicity = encoder_ethnicity.fit_transform(y_ethnicity)

encoder_gender = LabelEncoder()
y_gender = encoder_gender.fit_transform(y_gender)

# Dividir los datos en entrenamiento y prueba
X_train, X_test, y_train_age, y_test_age, y_train_ethnicity, y_test_ethnicity, y_train_gender, y_test_gender = train_test_split(
    X, y_age, y_ethnicity, y_gender, test_size=0.2, random_state=42)


In [57]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense

# Crear el modelo para predecir la edad
model_age = Sequential([
    Dense(128, activation='relu', input_shape=(X_train.shape[1],)),
    Dense(64, activation='relu'),
    Dense(1, activation='linear')  # Regresión para la edad
])

model_age.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])

# Entrenar el modelo para predecir la edad
model_age.fit(X_train, y_train_age, epochs=10, batch_size=32, validation_split=0.2)

# Evaluar el modelo en los datos de prueba
age_loss, age_mae = model_age.evaluate(X_test, y_test_age)
print(f'Mean Absolute Error para edad: {age_mae}')


C:\My programers\Anaconda3\lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 6s 7ms/step - loss: 472.3377 - mae: 16.2447 - val_loss: 268.0189 - val_mae: 12.3709
Epoch 2/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step - loss: 210.8202 - mae: 10.9046 - val_loss: 207.2066 - val_mae: 10.6527
Epoch 3/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step - loss: 174.7510 - mae: 9.8144 - val_loss: 196.6998 - val_mae: 10.3343
Epoch 4/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 2s 4ms/step - loss: 150.9673 - mae: 9.1180 - val_loss: 194.1596 - val_mae: 9.8944
Epoch 5/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step - loss: 138.5252 - mae: 8.7154 - val_loss: 197.6305 - val_mae: 10.3566
Epoch 6/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 2s 4ms/step - loss: 124.7602 - mae: 8.2826 - val_loss: 181.4782 - val_mae: 9.6329
Epoch 7/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 3s 6ms/step - loss: 118.3997 - mae: 8.0997 - val_loss: 202.0935 - val_mae: 10.1877
Epoch 8/10
475/475 ━━━━━━━━━━━━━━━━━━━━ 4s 8ms/step - loss: 120.5082 - mae: 8.1820 - val_loss: 165.5594 - val_mae: 9.1554
Epoch 9/10
475/47

In [62]:
# Preprocesar las imágenes y asegurarse de que tienen la forma correcta
def preprocess_image_from_csv(image_data):
    pixels = np.array(image_data.split(), dtype='float32')  # Convertir los datos de pixels en un array
    pixels = pixels.reshape(48, 48)  # Redimensionar la imagen (48x48 en escala de grises)
    pixels = np.expand_dims(pixels, axis=-1)  # Añadir una dimensión para el canal de color (escala de grises)
    pixels = pixels / 255.0  # Normalizar a [0, 1]
    return pixels

# 4. Preparar las imágenes y etiquetas para la predicción
X = np.array([preprocess_image_from_csv(img) for img in data['pixels']])
y = data[['age', 'gender', 'ethnicity']]  # Usamos las columnas de edad, género y etnia como etiquetas

# Asegúrate de que X tenga la forma (n_samples, 48, 48, 1)
X = X.reshape(-1, 48, 48, 1)  # Ajustar la forma de las imágenes

# Aplanar las imágenes antes de pasarlas al modelo
X_flat = X.reshape(X.shape[0], -1)  # Convertir cada imagen a un vector de tamaño 2304

# 5. Realizar las predicciones con el modelo
predictions = model_age.predict(X_flat)  # Usar X_flat para la predicción

predicted_age = model_age.predict(new_data)
print(f'Predicción de edad: {predicted_age[0]}')

# Predicción para etnia
predicted_ethnicity = model_ethnicity.predict(new_data)
predicted_ethnicity_label = encoder_ethnicity.inverse_transform([np.argmax(predicted_ethnicity)])
print(f'Predicción de etnia: {predicted_ethnicity_label[0]}')

# Predicción para género
predicted_gender = model_gender.predict(new_data)
predicted_gender_label = encoder_gender.inverse_transform([np.argmax(predicted_gender)])
print(f'Predicción de género: {predicted_gender_label[0]}')


741/741 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step


NameError: name 'new_data' is not defined

In [ ]:
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.models import load_model
from sklearn.metrics import accuracy_score, classification_report
from tensorflow.keras.preprocessing import image

# 1. Cargar el modelo previamente entrenado
model = load_model('face_model.h5')

# 2. Cargar el archivo CSV que contiene las imágenes y sus etiquetas
csv_file = 'age_gender.csv'  # Cambia esto por la ruta de tu archivo
data = pd.read_csv(csv_file)

# 3. Preprocesar las imágenes de acuerdo a cómo lo hiciste en el entrenamiento
def preprocess_image_from_csv(image_data):
    pixels = np.array(image_data.split(), dtype='float32')  # Convertir los datos de pixels en un array
    pixels = pixels.reshape(48, 48)  # Redimensionar la imagen (48x48 en escala de grises)
    pixels = np.expand_dims(pixels, axis=-1)  # Añadir una dimensión para el canal de color (escala de grises)
    pixels = pixels / 255.0  # Normalizar a [0, 1]
    return pixels

# 4. Preparar las imágenes y etiquetas para la predicción
X = np.array([preprocess_image_from_csv(img) for img in data['pixels']])
y = data[['age', 'gender', 'ethnicity']]  # Usamos las columnas de edad, género y etnia como etiquetas

# Asegúrate de que X tiene la forma (n_samples, 48, 48, 1)
X = X.reshape(-1, 48, 48, 1)  # Ajustar la forma de las imágenes

# 5. Realizar las predicciones con el modelo
predictions = model.predict(X)

# 6. Obtener las predicciones de edad, género y etnia
predicted_age = predictions[:, 0]  # Si el modelo tiene la edad como primera salida
predicted_gender = np.argmax(predictions[:, 1:3], axis=1)  # Asumimos que el género tiene 2 clases (masculino y femenino)
predicted_ethnicity = np.argmax(predictions[:, 3:], axis=1)  # Asumimos que la etnia tiene varias clases



# 7. Visualizar las predicciones junto con las etiquetas reales

i = 400

real_age = y.iloc[i]['age']
real_gender = y.iloc[i]['gender']
real_ethnicity = y.iloc[i]['ethnicity']

  
print(f"Imagen {200 + 1}:")
print(f"  Real -> Edad: {real_age}, Género: {'Masculino' if real_gender == 0 else 'Femenino'}, Etnia: {real_ethnicity}")
print(f"  Predicción -> Edad: {predicted_age[i]:.2f}, Género: {'Masculino' if predicted_gender[i] == 0 else 'Femenino'}, Etnia: {predicted_ethnicity[i]}")
print("-" * 40)
